## Preparing the Notebook

In [1]:
import numpy as np

import geopandas as gpd

import pandas as pd

# importing necessary libraries and packages
import requests
from zipfile import ZipFile
#import geopandas as gpd
import json
import plotly.express as px
import pandas as pd
import plotly.io as pio
import urllib

## Retrieving Municipalities and States' Shapefiles

## Loading json

In [2]:
gdf_munic = gpd.read_file('../data/territory/shp/BR_Municipios_2020.shp')

In [3]:
gdf_munic.info()

<class 'geopandas.geodataframe.GeoDataFrame'>
RangeIndex: 5570 entries, 0 to 5569
Data columns (total 6 columns):
 #   Column    Non-Null Count  Dtype   
---  ------    --------------  -----   
 0   CD_MUN    5570 non-null   object  
 1   NM_MUN    5570 non-null   object  
 2   SIGLA_UF  5570 non-null   object  
 3   AREA_KM2  5570 non-null   float64 
 4   CDMUN     5570 non-null   int64   
 5   geometry  5570 non-null   geometry
dtypes: float64(1), geometry(1), int64(1), object(3)
memory usage: 261.2+ KB


In [4]:
df_arranjos = pd.read_csv('../data/territory/list_arranjos_pop.csv', sep=';')

In [5]:
df_arranjos.columns = ['CD_MUN', 'Territory']

In [6]:
df_arranjos.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 5570 entries, 0 to 5569
Data columns (total 2 columns):
 #   Column     Non-Null Count  Dtype 
---  ------     --------------  ----- 
 0   CD_MUN     5570 non-null   int64 
 1   Territory  5570 non-null   object
dtypes: int64(1), object(1)
memory usage: 87.2+ KB


In [7]:
gdf_munic['CD_MUN'] = gdf_munic.CD_MUN.astype(np.int64)

In [8]:
gdf_munic = gdf_munic.merge(df_arranjos, on='CD_MUN')

In [9]:
gdf_munic = gdf_munic[~gdf_munic.Territory.str.startswith('Demais')]

In [11]:
gdf_munic

CD_MUN                       NM_MUN SIGLA_UF   AREA_KM2    CDMUN  \
111   1302603                       Manaus       AM  11401.092  1302603   
160   1500800                   Ananindeua       PA    190.581  1500800   
169   1501402                        Belém       PA   1059.466  1501402   
171   1501501                    Benevides       PA    187.826  1501501   
219   1504422                     Marituba       PA    103.214  1504422   
...       ...                          ...      ...        ...      ...   
5535  5219753  Santo Antônio do Descoberto       GO    945.650  5219753   
5546  5220454               Senador Canedo       GO    248.291  5220454   
5555  5221403                     Trindade       GO    710.328  5221403   
5563  5221858          Valparaíso de Goiás       GO     60.950  5221858   
5569  5300108                     Brasília       DF   5760.784  5300108   

                                               geometry          Territory  
111   POLYGON ((-60.24162 -1.99757, -60.23298 -2.003...    AP de Manaus/AM  
160   POLYGON ((-48.33466 -1.23983, -48.33379 -1.243...     AP de Belém/PA  
169   POLYGON ((-48.35304 -1.22103, -48.35754 -1.224...     AP de Belém/PA  
171   POLYGON ((-48.33104 -1.25695, -48.33038 -1.257...     AP de Belém/PA  
219   POLYGON ((-48.32070 -1.32335, -48.31987 -1.324...     AP de Belém/PA  
...                                                 ...                ...  
5535  POLYGON ((-48.36389 -15.81896, -48.36241 -15.8...  AP de Brasília/DF  
5546  POLYGON ((-49.07802 -16.59349, -49.07705 -16.5...   AP de Goiânia/GO  
5555  POLYGON ((-49.62145 -16.48975, -49.61954 -16.4...   AP de Goiânia/GO  
5563  POLYGON ((-48.01595 -16.04972, -48.01573 -16.0...  AP de Brasília/DF  
5569  POLYGON ((-47.41734 -15.54655, -47.41720 -15.5...  AP de Brasília/DF  

[214 rows x 7 columns]

In [10]:
gdf_munic.Territory.unique()

array(['AP de Manaus/AM', 'AP de Belém/PA', 'AP de Fortaleza/CE',
       'AP de Recife/PE', 'AP de Salvador/BA', 'AP de Belo Horizonte/MG',
       'AP de Vitória/ES', 'AP de Rio de Janeiro/RJ',
       'AP de São Paulo/SP', 'AP de Campinas/SP', 'AP de Curitiba/PR',
       'AP de Florianópolis/SC', 'AP de Porto Alegre/RS',
       'AP de Goiânia/GO', 'AP de Brasília/DF'], dtype=object)

In [12]:
files_names = ['manaus', 'belem', 'fortaleza','recife'
               , 'salvador', 'belo_horizonte', 'vitoria'
               , 'rio_de_janeiro', 'sao_paulo', 'campinas'
               , 'curitiba', 'florianópolis', 'porto_Alegre'
               , 'goiania', 'brasília']

for ap, file_name in zip(gdf_munic.Territory.unique(), files_names):
    
    lon = gdf_munic[gdf_munic['Territory'] == ap].dissolve('Territory').centroid.x[0];
    lat = gdf_munic[gdf_munic['Territory'] == ap].dissolve('Territory').centroid.y[0];
    
    minx, miny, maxx, maxy = gdf_munic[gdf_munic['Territory'] == ap].total_bounds
    max_bound = max(abs(maxx-minx), abs(maxy-miny)) * 111
    
    zoom = 13 - np.log(max_bound)

    fig = px.choropleth_mapbox(
        data_frame=gdf_munic[gdf_munic['Territory'] == ap]
        , geojson=gdf_munic[gdf_munic['Territory'] == ap]['geometry']
        , locations=gdf_munic[gdf_munic['Territory'] == ap].index
        , color='Territory'
        , center={'lat':lat, 'lon':lon}
        , zoom=zoom
        , mapbox_style='carto-positron'
        , opacity=0.4
        , color_discrete_sequence=['white']
        , height=600
        , width=1400
        , hover_name='NM_MUN'
        , hover_data=['CD_MUN']
    )
    
    fig.update_layout(margin=dict(l=0, r=0, b=0, t=1))

    fig.update_layout(showlegend=False)
    
    pio.write_json(fig=fig, file=f'../data/territory/json/plotly_fig/{file_name}.json');

C:\Users\augus\Anaconda3\envs\aulas\lib\site-packages\ipykernel_launcher.py:9: UserWarning:

Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.


C:\Users\augus\Anaconda3\envs\aulas\lib\site-packages\ipykernel_launcher.py:10: UserWarning:

Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.




ValueError: Value of 'hover_data_0' is not the name of a column in 'data_frame'. Expected one of ['CD_MUN', 'NM_MUN', 'SIGLA_UF', 'AREA_KM2', 'CDMUN', 'geometry', 'Territory'] but received: C

In [34]:
fig = pio.read_json('../data/territory/json/plotly_fig/curitiba.json')

In [35]:
fig

In [32]:
fig.update_layout(margin=dict(l=0, r=0, b=0, t=1))